# CO2 at Mauna Loa and Additive GPs in PyMC3

## The Keeling Curve

In the late 1950's Charles Keeling invented a accurate way to measure atmospheric CO$_2$ concentration and began taking regular measurements at the Mauna Loa observatory.  Today, measurements are continuously recorded.  Check out last hours measurement result [here].  

![Mauna Loa observatory](https://media.npr.org/assets/img/2013/05/08/mauna-loa-observatory_wide-38711aea834e72dcfc44eb93d7e2c184e88d361d.jpg?s=1400)

Not much was known about how fossil fuel burning influences the climate in the late 1950s.  The first couple years of data collection showed that CO$_2$ levels rose and fell following summer and winter, tracking the growth and decay of vegetation in the northern hemisphere.  As multiple years passed, the steady upward trend increasingly grew into focus.  With over 70 years of collected data, the Keeling curve is one of the most important climate indicators.

The history behind these measurements and their influence on climatology today and other interesting reading:

- http://scrippsco2.ucsd.edu/history_legacy/early_keeling_curve#
- https://scripps.ucsd.edu/programs/keelingcurve/2016/05/23/why-has-a-drop-in-global-co2-emissions-not-caused-co2-levels-in-the-atmosphere-to-stabilize/#more-1412
- http://cdiac.ornl.gov/

Let's load in the data, tidy it up, and have a look.  The [raw data set is located here](http://scrippsco2.ucsd.edu/data/atmospheric_co2/mlo).  This notebook uses the [Bokeh package](http://bokeh.pydata.org/en/latest/) for plots that benefit from interactivity.

In [1]:
import sys
sys.path.insert(0, "/home/bill/pymc3/")
import pymc3 as pm

import matplotlib.pyplot as plt
%matplotlib inline

import pandas as pd
import numpy as np
import theano.tensor as tt

In [2]:
data_monthly = pd.read_csv(pm.get_data("monthly_in_situ_co2_mlo.csv"), header=56)
 
# - replace -99.99 with NaN
data_monthly.replace(to_replace=-99.99, value=np.nan, inplace=True)

# fix column names
cols = ["year", "month", "--", "--", "CO2", "seasonaly_adjusted", "fit",
        "seasonally_adjusted_fit", "CO2_filled", "seasonally_adjusted_filled"]
data_monthly.columns = cols
cols.remove("--"); cols.remove("--")
data_monthly = data_monthly[cols]

# drop rows with nan
data_monthly.dropna(inplace=True)

# fix time index
data_monthly["day"] = 15
data_monthly.index = pd.to_datetime(data_monthly[["year", "month", "day"]])
cols.remove("year"); cols.remove("month")
data_monthly = data_monthly[cols]

data_monthly.head(5)

CO2  seasonaly_adjusted     fit  seasonally_adjusted_fit  \
1958-03-15  315.69              314.43  316.18                   314.90   
1958-04-15  317.46              315.15  317.30                   314.98   
1958-05-15  317.50              314.73  317.84                   315.06   
1958-07-15  315.86              315.17  315.87                   315.22   
1958-08-15  314.93              316.17  314.01                   315.29   

            CO2_filled  seasonally_adjusted_filled  
1958-03-15      315.69                      314.43  
1958-04-15      317.46                      315.15  
1958-05-15      317.50                      314.73  
1958-07-15      315.86                      315.17  
1958-08-15      314.93                      316.17

In [3]:
# format time to so that its useful for analysis
reference_time = pd.to_datetime('1958-03-15')
d = data_monthly.index - reference_time
t = d / pd.Timedelta(1, "Y")

# normalize CO2 levels
y = data_monthly["CO2"].values
first_co2 = y[0]
std_co2 = np.std(y)
y_n = (y - first_co2) / std_co2

data_monthly = data_monthly.assign(t = t)
data_monthly = data_monthly.assign(y_n = y_n)

This data might be familiar to you, since it was used as an example in the [Gaussian Processes for Machine Learning](http://www.gaussianprocess.org/gpml/) book by Rasmussen & Williams.  The version of the data set they use starts in the late 1950's, but stops at the end of 2003.  So that our PyMC3 example is somewhat comparable to their example, we use the stretch of data from before 2004 as the "training" set.  The data from 2004 to current we'll use to test our predictions. 

In [4]:
# split into training and test set
sep_idx = data_monthly.index.searchsorted(pd.to_datetime("2003-12-15"))
data_prior = data_monthly.iloc[:sep_idx+1, :]
data_after = data_monthly.iloc[sep_idx:, :]

In [36]:
# make plot
from bokeh.plotting import figure, show
from bokeh.palettes import Magma8
from bokeh.models import BoxAnnotation, Span, Label
from bokeh.io import output_notebook


output_notebook()
p = figure(x_axis_type='datetime', title='Monthly CO2 Readings from Mauna Loa',
           plot_width=700, plot_height=400)
p.yaxis.axis_label = 'CO2 [ppm]'
p.xaxis.axis_label = 'Date'
predict_region = BoxAnnotation(left=pd.to_datetime("2003-12-15"), 
                               fill_alpha=0.5, fill_color=Magma8[7])
p.add_layout(predict_region)
ppm400 = Span(location=400,
              dimension='width', line_color='red',
              line_dash='dashed', line_width=2)
p.add_layout(ppm400)

p.line(data_monthly.index, data_monthly['CO2'], 
       line_width=2, line_color=Magma8[0], alpha=0.5)
p.circle(data_monthly.index, data_monthly['CO2'], 
         line_color=Magma8[0], alpha=0.1, size=2)

train_label = Label(x=100, y=165, x_units='screen', y_units='screen',
                    text='Training Set', render_mode='css', border_line_alpha=0.0,
                    background_fill_alpha=0.0)
test_label  = Label(x=585, y=80, x_units='screen', y_units='screen',
                    text='Test Set', render_mode='css', border_line_alpha=0.0,
                    background_fill_alpha=0.0)

p.add_layout(train_label)
p.add_layout(test_label)
show(p)

Loading BokehJS ...

Bokeh plots are interactive, so panning and zooming can be done with the sidebar on the right hand side.  The seasonal rise and fall is plainly apparent, as is the upward trend.  Here is a link to an plots of [this curve at different time scales, and in the context of historical ice core data](https://scripps.ucsd.edu/programs/keelingcurve/).

The 400 ppm level is highlighted with a dashed line.  In addition to fitting a descriptive model, our goal will be to predict the first month the 400 ppm threshold is crossed, which was [May, 2013](https://scripps.ucsd.edu/programs/keelingcurve/2013/05/20/now-what/#more-741).  In the data set above, the CO$_2$ average reading for May, 2013 was about 399.98, close enough to be our correct target date. 

## Additive GPs ...

The GP implementation in PyMC3 is constructed so that it is easy to define additive GPs and sample from individual GP components.  

Consider two independent GP distributed functions, $f_1(x) \sim \mathcal{GP}\left(m_1(x),\, k_1(x, x')\right)$ and $f_2(x) \sim \mathcal{GP}\left( m_2(x),\, k_2(x, x')\right)$.  The joint distribution of $f_1$, $f_1^*$, $f_2$, $f_2^*$, $f_1 + f_2$ and $f_1^* + f_2^*$ is

$$
\begin{bmatrix} f_1 \\ f_1^* \\ f_2 \\ f_2^* 
             \\ f_1 + f_2    \\ f_1^* + f_2^* \end{bmatrix} \sim
  \text{N}\left( 
    \begin{bmatrix} m_1 \\ m_1^* \\ m_2 \\ m_2^* \\
                    m_1 + m_2    \\ m_1^* + m_2^*   \\ \end{bmatrix} \,,\,
    \begin{bmatrix} 
      K_1       &  K_1^*     &   0       &    0      & K_1        & K_1^*              \\
      K_1^{*^T} &  K_1^{**}  &   0       &    0      & K_1^*      & K_1^{**}           \\
      0         &  0         & K_2       & K_2^*     & K_2        & K_2^{*}            \\
      0         &  0         & K_2^{*^T} & K_2^{**}  & K_2^{*}    & K_2^{**}           \\
      K_1       &  K_1^{*}   & K_2       & K_2^{*}   & K_1 + K_2  & K_1^{*} + K_2^{*}  \\
 K_1^{*^T} & K_1^{**} & K_2^{*^T} & K_2^{**} & K_1^{*^T}+K_2^{*^T} & K_1^{**}+K_2^{**} 
    \end{bmatrix}
          \right) \,.
$$

Using the joint distribution to obtain the conditional distribution of $f_2^*$ with the contribution due to $f_1$ factored out, we get

$$
f_2^* \mid f_1 + f_2 \sim \text{N}\left(
  m_1^* + K_1^{*^T}(K_1 + K_2)^{-1}\left[f_1 + f_2 - m_1 - m_2\right] \,,\,
  K_1^{**} - K_1^{*^T}(K_1 + K_2)^{-1}K_1^* \right) \,.
$$

This formula gives the uncertainty for a GP component after marginalizing over the contributions from other components.  For more information, check out [David Duvenaud's PhD thesis](https://www.cs.toronto.edu/~duvenaud/thesis.pdf).

## ... in PyMC3

The GPs in PyMC3 keeps track of these marginals automatically.  The following code sketch shows how to define the conditional distribution of $f_2^*$.  We use `gp.Latent` in the example, but the same works for `gp.Marginal`.  The first block fits the GP prior.  We denote $f_1 + f_2$ as just $f$ for brevity.

    with pm.Model() as model:
        gp1 = pm.gp.Latent(mean_func1, cov_func1)
        gp2 = pm.gp.Latent(mean_func2, cov_func2)
        
        # gp represents f1 + f2.  
        gp = gp1 + gp2
        
        f = gp.prior("f", n_points, x)
        
        trace = pm.sample(1000)

The second block produces conditional distributions, including $f_2^* \mid f_1 + f_2$.  Notice that extra arguments are required for conditionals of $f1$ and $f2$, but not $f$.  This is because those arguments are cached when calling `.prior`.

    with model:
        # f_1^* | f_1 + f_2. Note that f = f1 + f2.
        f1_star = gp1.conditional("f1_star", n_star, X_star, X=X, f=f) 
        
        # f_2^* | f_1 + f_2
        f2_star = gp2.conditional("f2_star", n_star, X_star, X=X, f=f) 
        
        # f_1^* + f_2^* | f_1 + f_2.  X, f aren't required.
        f_star = gp.conditional("f_star", n_star, X_star)
        
`f1_star`, `f2_star`, and `f_star` are just PyMC3 random variables that can be either sampled from or incorporated into larger models.  

# Modeling the Keeling Curve using GPs

As a starting point, we use the GP model described in Rasmussen & Williams.  Instead of using flat priors on covariance function hyperparameters and then maximizing the marginal likelihood like is done in the textbook, we place somewhat informative priors on the hyperparameters and use the NUTS sampler for inference.  We use the `gp.Marginal` since Gaussian noise is assumed.

The R+W model is a sum of three GPs for the signal, and one GP for the noise.

1. A long term smooth rising trend represented by an exponentiated quadratic kernel.
2. A periodic term that decays away from exact periodicity.  This is represented by the product of a `Periodic` covariance function and an exponentiated quadratic.
3. Small and medium term irregularities with a rational quadratic kernel.

We use fairly uninformative priors for the scale hyperparameters of the covariance functions, and informative Gamma parameters for lengthscales.  The PDFs used for the lengthscale priors is shown below:

In [51]:
x = np.linspace(0, 150,10000)
priors = [
    ("ℓ1", pm.Gamma.dist(alpha=10, beta=0.075)),
    ("ℓp", pm.Gamma.dist(alpha=4,   beta=3)),
    ("ℓ2", pm.Gamma.dist(alpha=2.5, beta=0.5)),
    ("ℓ3", pm.Gamma.dist(alpha=4,   beta=0.1)),
    ("ℓn", pm.HalfCauchy.dist(beta=0.25))]

#for prior in priors:
#    plt.plot(x, np.exp(prior[1].logp(x).eval()), label=prior[0])

from bokeh.palettes import brewer
colors = brewer['Dark2'][5]

output_notebook()
p = figure(title='Monthly CO2 Readings from Mauna Loa',
           plot_width=700, plot_height=400)
p.yaxis.axis_label = 'CO2 [ppm]'
p.xaxis.axis_label = 'Date'

for i, prior in enumerate(priors):
    p.line(x, np.exp(prior[1].logp(x).eval()), legend=prior[0], 
           line_width=3, line_color=colors[i])
show(p)


Loading BokehJS ...

- $\ell 1$: The periodic decay.  The smaller this parameter is, the faster the periodicity goes away.  I doubt that the seasonality of the CO$_2$ will be going away any time soon (hopefully), and there's no evidence for that in the data.  Most of the prior mass is from 60 to >140 years.

- $\ell p$: The smoothness of the periodic component.  It controls how "sinusoidal" the periodcity is.  The plot of the data shows that seasonality is not an exact sine wave, but its not terribly different from one.  We use a Gamma whose mode is at one, and doesn't have too large of a variance, with most of the prior mass from 0.5 and 2.

- $\ell 2$:

- $\ell 3$:

- $\ell n$:

In [14]:
with pm.Model() as model:
    PosNormal = pm.Bound(pm.Normal, lower=0.0)
    
with model:
    # yearly periodic component x long term trend
    η1 = pm.HalfCauchy("η1", beta=5, testval=1.0)
    ℓ1 = pm.Gamma("ℓ1", alpha=3, beta=0.025, testval=75)
    p  = PosNormal("p", mu=1, sd=0.05, testval=1.0)
    ℓp = pm.Gamma("ℓp", alpha=2, beta=2, testval=1.0)
    cov_seasonal = η1**2 * pm.gp.cov.Periodic(1, ℓp, p) * pm.gp.cov.Matern52(1, ℓ1)
    gp_seasonal = pm.gp.Marginal(cov_func=cov_seasonal)
    
    # small/medium term irregularities
    η2 = pm.HalfCauchy("η2", beta=5, testval=1.0)
    ℓ2 = pm.Gamma("ℓ2", alpha=1.1, beta=0.2, testval=5.0)
    α = pm.HalfCauchy("α", beta=3, testval=2) # start with some diffusivity
    cov_medium = η2**2 * pm.gp.cov.RatQuad(1, ℓ2, α)
    gp_medium = pm.gp.Marginal(cov_func=cov_medium)
    
    # long term trend
    η3 = pm.HalfCauchy("η3", beta=5, testval=1.0)
    ℓ3 = pm.Gamma("ℓ3", alpha=3, beta=0.1, testval=50.0)
    cov_trend = η3**2 * pm.gp.cov.ExpQuad(1, ℓ3)
   
    # positive trend
    gp_trend = pm.gp.Marginal(cov_func=cov_trend)   

    # noise model
    ηn = pm.HalfNormal("ηn", sd=1, testval=0.1)
    ℓn = pm.Gamma("ℓn", alpha=1.05, beta=3, testval=0.5)
    σ  = pm.HalfNormal("σ",  sd=1, testval=0.05)
    cov_noise = ηn**2 * pm.gp.cov.Matern52(1, ℓn) +\
                pm.gp.cov.WhiteNoise(σ)
    
    gp = gp_seasonal + gp_medium + gp_trend
    
    y_ = gp.marginal_likelihood("y_", n_points=t.shape[0], X=t, y=y, noise=cov_noise)
    mp = pm.find_MAP(method="L-BFGS-B")
    #tr = pm.sample(1000)

lp = 1,640.4, ||grad|| = 173.52:   1%|          | 405/50000 [02:17<4:44:48,  2.90it/s]   


In [11]:
# display the results
sorted([name+":"+str(mp[name]) for name in mp.keys() if not name.endswith("_")])

['α:27354164363264.0',
 'η1:1.561810851097107',
 'η2:0.2438364326953888',
 'η3:46028688.0',
 'ηn:0.17089249193668365',
 'σ:0.08165835589170456',
 'ℓ1:29.90250015258789',
 'ℓ2:2.803438186645508',
 'ℓ3:62473.3125',
 'ℓn:0.9317159652709961',
 'ℓp:0.9554763436317444']

In [ ]:
# predict total
n = len(data_monthly)
Xnew = np.concatenate((np.ones((n, 1)), data_monthly["t"].values[:,None]),1)

n_draws = 50
with model:
    f_pred = gp.conditional("f_pred", n_points=n, Xnew=Xnew)
    samples = pm.sample_ppc([mp], vars=[f_pred], samples=n_draws)

In [36]:
preds = samples[f_pred.name]*std_co2 + first_co2

## make plot
p = figure(x_axis_type='datetime', plot_width=700, plot_height=300)

# previous plot
p.yaxis.axis_label = 'CO2 [ppm]'
p.xaxis.axis_label = 'Date'

p.line(data_monthly.index, data_monthly['CO2'], 
       line_width=1, line_color="black")

predict_region = BoxAnnotation(left=pd.to_datetime("2003-12-15"), 
                               fill_alpha=0.1, fill_color='firebrick')
ppm400 = Span(location=400,
              dimension='width', line_color='black',
              line_dash='dashed', line_width=1)
p.add_layout(predict_region)
p.add_layout(ppm400)

# predictions
p.multi_line([data_monthly.index]*n_draws, [preds[i,:] for i in range(n_draws)],
             color="green", alpha=0.05)
show(p)



In [46]:
with model:
    f_seasonal = gp_seasonal.conditional("f_seasonal", n_points=n, 
                                         Xnew=Xnew, X=X, y=y_n, noise=cov_noise)
    samples = pm.sample_ppc([mp], vars=[f_seasonal], samples=n_draws)

100%|██████████| 50/50 [00:23<00:00,  2.88it/s]


In [47]:
preds = samples[f_seasonal.name]*std_co2 + mean_co2

## make plot
p = figure(x_axis_type='datetime', plot_width=700, plot_height=300)

# previous plot
p.yaxis.axis_label = 'CO2 [ppm]'
p.xaxis.axis_label = 'Date'

p.line(data_monthly.index, data_monthly['CO2'], 
       line_width=1, line_color="black")

predict_region = BoxAnnotation(left=pd.to_datetime("2003-12-15"), 
                               fill_alpha=0.1, fill_color='firebrick')
#ppm400 = Span(location=400,
#              dimension='width', line_color='black',
#              line_dash='dashed', line_width=1)
p.add_layout(predict_region)
#p.add_layout(ppm400)

# predictions
p.multi_line([data_monthly.index]*n_draws, [preds[i,:] for i in range(n_draws)],
             color="green", alpha=0.05)
show(p)

In [39]:
with model:
    f_medium = gp_medium.conditional("f_medium", n_points=n,
                                     Xnew=Xnew, X=X, y=y_n, noise=cov_noise)
    samples = pm.sample_ppc([mp], vars=[f_medium], samples=n_draws)

100%|██████████| 50/50 [00:21<00:00,  2.44it/s]


In [40]:
preds = samples[f_medium.name]*std_co2 + mean_co2

## make plot
p = figure(x_axis_type='datetime', plot_width=700, plot_height=300)

# previous plot
p.yaxis.axis_label = 'CO2 [ppm]'
p.xaxis.axis_label = 'Date'

predict_region = BoxAnnotation(left=pd.to_datetime("2003-12-15"), 
                               fill_alpha=0.1, fill_color='firebrick')
#ppm400 = Span(location=400,
#              dimension='width', line_color='black',
#              line_dash='dashed', line_width=1)
p.add_layout(predict_region)
#p.add_layout(ppm400)

# predictions
p.multi_line([data_monthly.index]*n_draws, [preds[i,:] for i in range(n_draws)],
             color="green", alpha=0.05)
show(p)

In [41]:
with model:
    f_trend = gp_trend.conditional("f_trend", n_points=n,
                                   Xnew=Xnew, X=X, y=y_n, noise=cov_noise) 
    samples = pm.sample_ppc([mp], vars=[f_trend], samples=n_draws)

100%|██████████| 50/50 [00:17<00:00,  3.42it/s]


In [42]:
preds = samples[f_trend.name]*std_co2 + mean_co2

## make plot
p = figure(x_axis_type='datetime', plot_width=700, plot_height=300)

# previous plot
p.yaxis.axis_label = 'CO2 [ppm]'
p.xaxis.axis_label = 'Date'

p.line(data_monthly.index, data_monthly['CO2'], 
       line_width=1, line_color="black")

predict_region = BoxAnnotation(left=pd.to_datetime("2003-12-15"), 
                               fill_alpha=0.1, fill_color='firebrick')
#ppm400 = Span(location=400,
#              dimension='width', line_color='black',
#              line_dash='dashed', line_width=1)
p.add_layout(predict_region)
#p.add_layout(ppm400)

# predictions
p.multi_line([data_monthly.index]*n_draws, [preds[i,:] for i in range(n_draws)],
             color="green", alpha=0.05)
show(p)

In [13]:
t = data_prior["t"].values[:,None]
y = data_prior["y_n"].values

(545, 1) (545,)


In [17]:
results = sorted([name+":"+str(mp[name]) for name in mp.keys() if not name.endswith("_")])

In [19]:
results

['p:0.9997539520263672',
 'α:2.795670509338379',
 'η1:0.11767382174730301',
 'η2:0.35704460740089417',
 'η3:2.6173551082611084',
 'ηn:0.01685485430061817',
 'σ:0.0077663869597017765',
 'ℓ1:129.4181365966797',
 'ℓ2:17.919713973999023',
 'ℓ3:46.77431869506836',
 'ℓn:0.5263724327087402',
 'ℓp:0.7778873443603516']